Pakai BM25L, Jaccard, BM25

In [1]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import re
from sklearn.metrics.pairwise import cosine_similarity
import matplotlib.pyplot as plt

In [2]:
# read data
import pandas as pd
dataset = pd.read_csv('data uas nlp2.csv', sep = ';') #dataset asli tanpa dihapus yang missval
gt = pd.read_csv('List Query NLP - Index Ground Truth.csv') 
# Jika ada NaN atau missing value, isi dengan angka placeholder (-1) lalu ubah ke integer
dataset["Index"] = dataset["Index"].fillna(-1).astype(int) ### missing value diganti jadi -1 soalnyaa dataset ada yg kosong jadi ngaruh ke index tp aku ttp aku pake df["Index"] dari dataset



In [3]:
dataset= dataset[["Index","Headline",	"Author Name",	"Details",	"Description",	"Infomation",	"Nutrition",	"Serving",	"Rating",	"Rating Count",	"Category",	"Cuisine",	"Ingredients",	"Instruction"]]

In [4]:
"""Pakai lemmatizer + stopwords 
karena hasilnya membaik setelah prepro pakai ini"""

import pandas as pd
import re
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

# Download necessary NLTK resources
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')
lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words('english'))

def preprocess_text(text):
    if pd.isna(text):
        return ""
    text = str(text).lower()
    text = re.sub(r"[{}:.,!?;\"'()\-]", "", text)  
    text = re.sub(r"Â", "", text)    
    text = re.sub(r"[^\x00-\x7F]+", "", text)  
    text = re.sub(r"\s+", " ", text).strip()   
    tokens = word_tokenize(text) 

    filtered_tokens = [lemmatizer.lemmatize(token) for token in tokens if token not in stop_words]

    return ' '.join(filtered_tokens)  

dataset = dataset.drop_duplicates()

columns = [col for col in dataset.columns if col != 'Index']
dataset['dokumen'] = dataset.apply(lambda x: ' '.join([str(x[col]) if pd.notna(x[col]) else '' for col in columns]), axis=1)
dataset['processed_text'] = dataset['dokumen'].apply(preprocess_text)

# Select relevant columns to display
result = dataset[['Index', 'Headline', 'processed_text']]
print(result)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\rashi\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\rashi\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\rashi\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


      Index                                           Headline  \
0         0  Eva Longoria’s 5-Ingredient Loaded Sweet Potatoes   
1         1  French Onion Cabbage Soup Is a Fun Twist on th...   
2         2   Making Cheesy Cabbage Gratin Is Worth the Effort   
3         3  Pumpkin-Summer Squash Ravioli with Brown Butte...   
4         4                           This Orange Chicken &amp   
...     ...                                                ...   
5185   6802                       Slow-Cooker Korean Beef &amp   
5186   6803                      One-Pot Creamy Vegetable Soup   
5187   6804                     Slow-Cooker Carrot-Leek Bisque   
5188   6805                 Slow-Cooker Italian Vegetable &amp   
5189   6865               How to Make Popcorn in the Microwave   

                                         processed_text  
0     eva longorias 5ingredient loaded sweet potato ...  
1     french onion cabbage soup fun twist classic me...  
2     making cheesy cabbage grati

In [5]:
dataset['processed_text'].head()

0    eva longorias 5ingredient loaded sweet potato ...
1    french onion cabbage soup fun twist classic me...
2    making cheesy cabbage gratin worth effort juli...
3      pumpkinsummer squash ravioli brown butter & amp
4                                 orange chicken & amp
Name: processed_text, dtype: object

In [6]:
import pandas as pd
data = {
    "pertanyaan": [
        "any dinner recipes?",
        "Which recipes include both chicken and broccoli as ingredients and have a Mediterranean diet classification?",
        "Are there nut-free recipes?",
        "Gluten-free recipes for diet",
        "Vegan dinner recipes categorized as low-carb",
        "High-protein recipes containing quinoa as a primary ingredient",
        "asian dinner food",
        "Dessert from America",
        "Dishes free from added sugar",
        "Dessert with chocolate",
        "High protein meal for vegetarian",
        "Low sugar and less than 150 calories drink suit for diabetic",
        "No-bake dessert recipes that are simple and quick to make",
        "Provide meal prep recipes designed for weight loss with no seafood",
        "Low-carb and high protein meals suitable for keto diet",
        "Plant-based recipes high in iron for vegans",
        "Low-sodium soups with fresh ingredients",
        "Up to 4.5 star ratings smoothie bowl with banana",
        "Fermented drinks for gut health and digestion",
        "Low calorie dinner meal with lamb",
        "Show me a recipe with sweet potatoes.",
        "I need a Mediterranean Diet dinner recipe.",
        "What are the recipes authored by Julia Levy?",
        "Can you show me a vegetarian soup recipe?",
        "Show recipes with a rating greater than 4 stars and chicken as a main ingredient.",
        "Do you have any protein-packed chicken dishes?",
        "Find me recipes for dinner?",
        "List breakfast recipes with a 5-star rating.",
        "Can you show nut-free mexican recipes?",
        "Find me a dish without added sugar.",
        "I want halal mexican food",
        "Give me vegan recipe under 20 minutes",
        "Find me dessert recipe under 100 calories",
        "Breakfast recipe with no egg",
        "Soup recipe for 4 servings",
        "I want a snack recipe with high protein",
        "Give me a salmon recipe with no oven require",
        "Breakfast recipe for lactose intolerant",
        "Recipe for bone health",
        "Give me a dessert recipe that is diabetes friendly",
        "peanut butter pancakes for breakfast",
        "cook shrimp pad Thai",
        "Egg-avocado breakfast sandwich",
        "broccoli and sun-dried tomato pasta salad recipe",
        "smoothie recipes with antioxidants",
        "Easy lemon recipes",
        "pumpkin sugar cookies that stay soft",
        "quinoa salad with feta, olives, and tomatoes",
        "penne with tuna and sun-dried tomatoes",
        "recipe for a cucumber sandwich",
        "Show me a recipe with lamb and garlic",
        "I need a breakfast recipe that serves two people less than 30 minutes",
        "Show me a recipe provided by liv dansky",
        "i am looking for a slow cooker recipe that take more than 3 hours",
        "Find me some dish that didn't add any kind of beans",
        "list a recipes for a 5 star rating chicken dish",
        "show recipes for asia continent",
        "looking for a cake with low calories",
        "show me a recipe without any milk or lactose",
        "give me a diet dish contains no vegetable"
    ]
}

queries = pd.DataFrame(data)
queries['processed_pertanyaan'] = queries['pertanyaan'].apply(lambda text: preprocess_text(text))
print(queries)


                                           pertanyaan  \
0                                 any dinner recipes?   
1   Which recipes include both chicken and broccol...   
2                         Are there nut-free recipes?   
3                        Gluten-free recipes for diet   
4        Vegan dinner recipes categorized as low-carb   
5   High-protein recipes containing quinoa as a pr...   
6                                   asian dinner food   
7                                Dessert from America   
8                        Dishes free from added sugar   
9                              Dessert with chocolate   
10                   High protein meal for vegetarian   
11  Low sugar and less than 150 calories drink sui...   
12  No-bake dessert recipes that are simple and qu...   
13  Provide meal prep recipes designed for weight ...   
14  Low-carb and high protein meals suitable for k...   
15        Plant-based recipes high in iron for vegans   
16            Low-sodium soups 

In [7]:
import pandas as pd
ground_truth = gt
gtruth = {}

for col in ground_truth.columns:
    if col.startswith('q'):  
        question_key = f"Pertanyaan {col[1:]}"  # 'q1' -> 'Pertanyaan 1'
        
        gtruth[question_key] = set(ground_truth[col].dropna().astype(int).tolist())
print(gtruth)

{'Pertanyaan 1': {0, 1, 2, 3, 4, 5, 6, 8, 4104, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 4125, 38, 40, 43, 4142, 47, 4153, 4163, 80, 2129, 82, 4177, 84, 85, 4180, 4562, 4196, 2150, 4201, 2154, 4563, 114, 2165, 118, 2167, 4237, 4248, 4250, 4251, 160, 161, 162, 2214, 168, 169, 171, 176, 2226, 179, 181, 182, 183, 184, 4280, 186, 187, 188, 189, 190, 191, 4283, 4289, 194, 195, 4292, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 2258, 4315, 4316, 2269, 4319, 4324, 4116, 4568, 4333, 4336, 4342, 4343, 4344, 4366, 272, 273, 4368, 276, 277, 278, 279, 281, 283, 2334, 288, 289, 291, 292, 4388, 4389, 295, 4391, 297, 299, 4395, 4398, 303, 4402, 307, 308, 4403, 310, 312, 4408, 4409, 315, 316, 318, 323, 324, 4424, 333, 4429, 335, 4430, 4434, 4438, 4439, 344, 345, 347, 350, 355, 357, 358, 359, 4549, 361, 363, 364, 366, 4464, 369, 372, 373, 374, 375, 376, 4552, 378, 379, 380, 381, 382, 383, 384, 386, 388, 4485, 390, 391, 4487,

# BM25L dan Boolean Function digabung

In [11]:
import re
from math import log

class BooleanBM25LRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist() 
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        self.index = self._create_index()
        self.doc_lengths = self._calculate_doc_lengths()
        self.avgdl = sum(self.doc_lengths.values()) / len(self.doc_lengths)
    
        self.k1 = 2.0
        self.b = 0.5
        self.delta = 0.75

    def _create_index(self):
        index = {}
        for doc_id, content in zip(self.doc_ids, self.documents):
            terms = content.lower().split()
            for term in terms:
                if term not in index:
                    index[term] = set()
                index[term].add(doc_id)  
        return index

    def _calculate_doc_lengths(self):
        return {doc_id: len(content.split()) for doc_id, content in zip(self.doc_ids, self.documents)}
    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)
    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms
    def _calculate_bm25l_score(self, term, doc_id):
        if term not in self.index or doc_id not in self.index[term]:
            return 0
        doc_terms = self.documents[self.doc_ids.index(doc_id)].lower().split()
        tf = doc_terms.count(term)
        df = len(self.index[term])
        N = len(self.documents)
        idf = log((N - df + 0.5) / (df + 0.5))
        dl = self.doc_lengths[doc_id]
        ctd = tf / (1 - self.b + self.b * dl / self.avgdl)
        tf_bm25l = (ctd + self.delta) / (self.k1 + ctd + self.delta)
        return idf * tf_bm25l
    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        relevant_docs = set(self.doc_ids)
        
        for term in negative_terms:
            if term in self.index:
                relevant_docs -= self.index[term]
        scores = {}
        if positive_terms:
            for doc_id in relevant_docs:
                score = sum(self._calculate_bm25l_score(term, doc_id) for term in positive_terms)
                if score > 0:
                    scores[doc_id] = score
        else:
            for doc_id in relevant_docs:
                scores[doc_id] = self.doc_lengths[doc_id]
        ranked_results = sorted(scores.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results
    
# # Menghitung Reciprocal Rank (RR) untuk setiap query
# def calculate_rr(results_dict, ground_truth_dict):
#     """
#     Menghitung Reciprocal Rank (RR) untuk setiap query.

#     Parameters:
#     - results_dict: Dict hasil pencarian dengan format:
#         {query: {'Index': [list of document indices], 'Scores': [list of scores]}}
#     - ground_truth_dict: Dict *ground truth* dengan format:
#         {query: [list of relevant document indices]}

#     Returns:
#     - rr_scores: Dict dengan Reciprocal Rank untuk setiap query.
#     """
#     rr_scores = {}
#     for query, results in results_dict.items():
#         retrieved_indices = results['Index']
#         ground_truth = ground_truth_dict.get(query.lower(), [])

#         # Cari posisi dokumen relevan pertama dalam hasil pencarian
#         rank = 0
#         for i, doc_id in enumerate(retrieved_indices):
#             if doc_id in ground_truth:
#                 rank = i + 1  # Rank dihitung dari indeks ke-1
#                 break

#         # Hitung Reciprocal Rank (RR)
#         rr_scores[query] = 1 / rank if rank > 0 else 0

#     return rr_scores

# # Menghitung MRR (Mean Reciprocal Rank)
# def calculate_mrr(rr_scores):
#     """
#     Menghitung Mean Reciprocal Rank (MRR) dari semua query.

#     Parameters:
#     - rr_scores: Dict dengan Reciprocal Rank untuk setiap query.

#     Returns:
#     - MRR (float): Nilai rata-rata Reciprocal Rank.
#     """
#     return sum(rr_scores.values()) / len(rr_scores) if rr_scores else 0

In [9]:
# BM25L BARU
# import re
# from math import log
# from collections import Counter, defaultdict
# from typing import List, Set, Tuple, Dict, Optional
# import numpy as np

# class BooleanBM25LRetrieval:
#     def __init__(self, 
#                  df, 
#                  df_pertanyaan, 
#                  k1: float = 2.0, 
#                  b: float = 0.5, 
#                  delta: float = 0.75,
#                  min_df: int = 2,
#                  max_df_ratio: float = 0.95):
#         """
#         Initialize the BM25L retrieval system with boolean query capabilities.
        
#         Args:
#             df: DataFrame containing documents
#             df_pertanyaan: DataFrame containing queries
#             k1: BM25L parameter for term frequency scaling
#             b: BM25L parameter for length normalization
#             delta: BM25L parameter for term frequency normalization
#             min_df: Minimum document frequency for a term to be included
#             max_df_ratio: Maximum ratio of documents a term can appear in
#         """
#         self._validate_input(df, df_pertanyaan)
        
#         self.documents = df["processed_text"].tolist()
#         self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
#         self.doc_ids = df["Index"].tolist()
        
#         self.k1 = k1
#         self.b = b
#         self.delta = delta
#         self.min_df = min_df
#         self.max_df = int(len(self.documents) * max_df_ratio)
        
#         # Boolean query operators
#         self.operators = {
#             'AND': '&',
#             'OR': '|',
#             'NOT': '!',
#             'without': '!',
#             'but': '!',
#             'no': '!'
#         }
        
#         # Build index and calculate statistics
#         self.index = self._create_index()
#         self.doc_lengths = self._calculate_doc_lengths()
#         self.avgdl = np.mean(list(self.doc_lengths.values()))
#         self.idf_cache = self._calculate_idfs()
        
#         # Precompute document vectors for faster scoring
#         self.doc_vectors = self._precompute_doc_vectors()

#     def _validate_input(self, df, df_pertanyaan):
#         """Validate input DataFrames"""
#         required_columns = {
#             'documents': ['processed_text', 'Index'],
#             'queries': ['processed_pertanyaan']
#         }
        
#         for col in required_columns['documents']:
#             if col not in df.columns:
#                 raise ValueError(f"Column '{col}' missing from documents DataFrame")
                
#         for col in required_columns['queries']:
#             if col not in df_pertanyaan.columns:
#                 raise ValueError(f"Column '{col}' missing from queries DataFrame")

#     def _create_index(self) -> Dict[str, Dict[int, int]]:
#         """
#         Create an inverted index with term frequencies.
#         Returns: Dict[term -> Dict[doc_id -> term_freq]]
#         """
#         index = defaultdict(lambda: defaultdict(int))
#         doc_freqs = Counter()
        
#         for doc_id, content in zip(self.doc_ids, self.documents):
#             terms = content.lower().split()
#             term_counts = Counter(terms)
            
#             for term, count in term_counts.items():
#                 index[term][doc_id] = count
#                 doc_freqs[term] += 1
        
#         # Filter terms based on document frequency
#         filtered_index = {
#             term: postings for term, postings in index.items()
#             if self.min_df <= doc_freqs[term] <= self.max_df
#         }
        
#         return filtered_index

#     def _calculate_doc_lengths(self) -> Dict[int, int]:
#         """Calculate document lengths"""
#         return {
#             doc_id: len(content.split()) 
#             for doc_id, content in zip(self.doc_ids, self.documents)
#         }

#     def _calculate_idfs(self) -> Dict[str, float]:
#         """Precompute IDF values for all terms"""
#         N = len(self.documents)
#         return {
#             term: log((N - len(postings) + 0.5) / (len(postings) + 0.5))
#             for term, postings in self.index.items()
#         }

#     def _precompute_doc_vectors(self) -> Dict[int, Dict[str, float]]:
#         """Precompute BM25L scores for each term in each document"""
#         doc_vectors = defaultdict(dict)
        
#         for term, postings in self.index.items():
#             idf = self.idf_cache[term]
            
#             for doc_id, tf in postings.items():
#                 dl = self.doc_lengths[doc_id]
#                 ctd = tf / (1 - self.b + self.b * dl / self.avgdl)
#                 tf_bm25l = (ctd + self.delta) / (self.k1 + ctd + self.delta)
#                 doc_vectors[doc_id][term] = idf * tf_bm25l
                
#         return doc_vectors

#     def _parse_boolean_query(self, query: str) -> Tuple[List[str], List[str]]:
#         """
#         Parse boolean query into positive and negative terms.
#         Handles complex boolean expressions with AND, OR, NOT operators.
#         """
#         query = query.lower()
#         for original, replacement in self.operators.items():
#             query = query.replace(original.lower(), replacement)
            
#         # Split on operators while preserving them
#         tokens = re.findall(r'[!&|]|\b\w+\b', query)
        
#         positive_terms = []
#         negative_terms = []
#         i = 0
        
#         while i < len(tokens):
#             if tokens[i] == '!':
#                 if i + 1 < len(tokens):
#                     negative_terms.append(tokens[i + 1])
#                     i += 2
#             elif tokens[i] not in {'&', '|'}:
#                 positive_terms.append(tokens[i])
#                 i += 1
#             else:
#                 i += 1
                
#         return positive_terms, negative_terms

#     def search(self, query: str, top_n: int = 5) -> List[Tuple[int, float]]:
#         """
#         Search documents using boolean BM25L ranking.
        
#         Args:
#             query: Search query with boolean operators
#             top_n: Number of top results to return
            
#         Returns:
#             List of (doc_id, score) tuples
#         """
#         positive_terms, negative_terms = self._parse_boolean_query(query)
        
#         # Filter out documents containing negative terms
#         candidate_docs = set(self.doc_ids)
#         for term in negative_terms:
#             if term in self.index:
#                 candidate_docs -= set(self.index[term].keys())
        
#         # Score remaining documents
#         scores = {}
#         if positive_terms:
#             for doc_id in candidate_docs:
#                 if doc_id in self.doc_vectors:
#                     score = sum(
#                         self.doc_vectors[doc_id].get(term, 0)
#                         for term in positive_terms
#                     )
#                     if score > 0:
#                         scores[doc_id] = score
#         else:
#             # If no positive terms, rank by document length
#             scores = {
#                 doc_id: 1 / self.doc_lengths[doc_id]
#                 for doc_id in candidate_docs
#             }
            
#         return sorted(scores.items(), key=lambda x: x[1], reverse=True)[:top_n]

#### Calculate Metrics


In [10]:
def calculate_metrics(results_dict, ground_truth_dict):
    precision_list = []
    recall_list = []
    for query, group in results_dict.items():
        true_positives = 0
        false_positives = 0
        ground_truth = ground_truth_dict.get(query, set())
       
        retrieved_docs = set(group['Index']) 
        correct_products = []
        incorrect_products = []
        for doc in retrieved_docs:
            if doc in ground_truth:
                true_positives += 1
                correct_products.append(doc)
            else:
                false_positives += 1
                incorrect_products.append(doc)
        false_negatives = len(ground_truth) - true_positives
        precision = (
            true_positives / (true_positives + false_positives)
            if (true_positives + false_positives) > 0
            else 0
        )
        recall = (
            true_positives / (true_positives + false_negatives)
            if (true_positives + false_negatives) > 0
            else 0
        )
        precision_list.append(precision)
        recall_list.append(recall)
        missing_products = ground_truth - retrieved_docs
        print(f"\nEvaluating {query}:")
        print("Correct Indices:", correct_products)
        print("Incorrect Indices:", incorrect_products)
        print("Missing Indices:", list(missing_products))
    avg_precision = (
        sum(precision_list) / len(precision_list) if precision_list else 0
    )
    avg_recall = sum(recall_list) / len(recall_list) if recall_list else 0
    print("\nEvaluation Metrics:")
    print(f"Average Precision: {avg_precision:.3f}")
    print(f"Average Recall: {avg_recall:.3f}")
    return avg_precision, avg_recall

#### Function display

In [11]:

def display_search_results(retrieval, query, results):
    print("\n" + "="*50)
    print(f"Query: {query}")
    print("="*50)
    
    if not results:
        print("Tidak ditemukan hasil yang relevan.")
        return
    
    print(f"Top {len(results)} hasil pencarian:")
    print("-"*50)
    
    for rank, (doc_id, score) in enumerate(results, 1):
        doc_text = retrieval.documents[retrieval.doc_ids.index(doc_id)]
        doc_preview = doc_text[:200] + "..." if len(doc_text) > 200 else doc_text
        
        print(f"\nRank {rank}:")
        print(f"Document ID: {doc_id}")
        print(f"Score: {score:.4f}")
        print(f"Preview: {doc_preview}")
        print("-"*50)

### Top-5

#### Evaluasi Metrik Shiqa

In [12]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
top_5 = int(5)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_5)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 5 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 1.3151
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 1.3151
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 4661
Score: 1.2817
Preview: easy baked fish fillet jane doerfer prep time 10 min total time 30 min serving 4 looking simple fish dinner skip frozen fillet try easy recipe baked fresh fish fillet little prep involved great lastmi...
-----------------------------------------

### Evaluasi Metrik Shiba

In [12]:
def evaluate_retrieval(ground_truth_dict, query_id, retrieved_indices):
    relevant_indices = ground_truth_dict.get(query_id, set())
    retrieved_set = set(retrieved_indices)

    tp = len(retrieved_set & relevant_indices)  # True positives
    fp = len(retrieved_set - relevant_indices)  # False positives
    fn = len(relevant_indices - retrieved_set)  # False negatives

    precision = tp / (tp + fp) if tp + fp > 0 else 0
    recall = tp / (tp + fn) if tp + fn > 0 else 0

    return precision, recall

def calculate_metrics2(results_dict, ground_truth_dict):
    precision_list = []
    recall_list = []
    for query, group in results_dict.items():
        # Ambil hasil dari ground_truth_dict
        relevant_docs = ground_truth_dict.get(query, set())
        
        # Indeks dokumen yang diambil berdasarkan hasil pencarian
        retrieved_docs = set(group['Index'])
        
        # Hitung TP, FP, FN
        tp = len(retrieved_docs & relevant_docs)
        fp = len(retrieved_docs - relevant_docs)
        fn = len(relevant_docs - retrieved_docs)
        
        # Hitung precision dan recall
        precision = tp / (tp + fp) if tp + fp > 0 else 0
        recall = tp / (tp + fn) if tp + fn > 0 else 0
        
        precision_list.append(precision)
        recall_list.append(recall)
        
        print(f"\nEvaluating query: {query}")
        print(f"Precision: {precision:.3f}, Recall: {recall:.3f}")
        
    # Menghitung nilai rata-rata untuk precision dan recall
    avg_precision = sum(precision_list) / len(precision_list) if precision_list else 0
    avg_recall = sum(recall_list) / len(recall_list) if recall_list else 0
    
    print("\nFinal Evaluation Metrics:")
    print(f"Average Precision: {avg_precision:.3f}")
    print(f"Average Recall: {avg_recall:.3f}")
    
    return avg_precision, avg_recall

# Evaluasi hasil pencarian
print("\nEvaluating Retrieval Performance")
average_precision, average_recall = evaluate_retrieval(results_dict, ground_truth_dict)



Evaluating Retrieval Performance


NameError: name 'ground_truth_dict' is not defined

### RR

In [14]:
df = dataset
df_pertanyaan = queries

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_5)
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }

# Hitung Reciprocal Rank dan MRR
rr_scores = calculate_rr(results_dict, ground_truth_dict)
mrr_score = calculate_mrr(rr_scores)

# Tampilkan hasil evaluasi
print("\nHasil Evaluasi Reciprocal Rank (RR):")
print("="*50)
for query, rr in rr_scores.items():
    print(f"Query: {query} | RR: {rr:.4f}")

print("\nMean Reciprocal Rank (MRR):")
print(f"MRR: {mrr_score:.4f}")



Hasil Evaluasi Reciprocal Rank (RR):
Query: dinner recipe | RR: 1.0000
Query: recipe include chicken broccoli ingredient mediterranean diet classification | RR: 0.5000
Query: nutfree recipe | RR: 1.0000
Query: glutenfree recipe diet | RR: 1.0000
Query: vegan dinner recipe categorized lowcarb | RR: 0.0000
Query: highprotein recipe containing quinoa primary ingredient | RR: 1.0000
Query: asian dinner food | RR: 1.0000
Query: dessert america | RR: 0.2000
Query: dish free added sugar | RR: 1.0000
Query: dessert chocolate | RR: 1.0000
Query: high protein meal vegetarian | RR: 0.0000
Query: low sugar less 150 calorie drink suit diabetic | RR: 0.0000
Query: nobake dessert recipe simple quick make | RR: 0.2500
Query: provide meal prep recipe designed weight loss seafood | RR: 1.0000
Query: lowcarb high protein meal suitable keto diet | RR: 0.5000
Query: plantbased recipe high iron vegan | RR: 0.0000
Query: lowsodium soup fresh ingredient | RR: 0.5000
Query: 45 star rating smoothie bowl banana

1. Reciprocal Rank (RR)
RR adalah nilai yang menunjukkan pada posisi ke berapa dokumen relevan pertama ditemukan dalam daftar hasil pencarian. Jika dokumen relevan pertama ditemukan pada posisi ke-1, maka RR = 1. Jika dokumen relevan tidak ditemukan, maka RR = 0.

`Query: "show recipe asia continent" | RR: 0.0000`
`Tidak ada dokumen relevan dalam hasil pencarian untuk query ini.`
`Query: "looking cake low calorie" | RR: 1.0000`
`Dokumen relevan ditemukan di posisi pertama dalam hasil pencarian.`
`Query: "show recipe without milk lactose" | RR: 0.0000`
`Tidak ada dokumen relevan dalam hasil pencarian untuk query ini.`
`Query: "give diet dish contains vegetable" | RR: 0.0000`
`Tidak ada dokumen relevan dalam hasil pencarian untuk query ini.`

2. Mean Reciprocal Rank (MRR)
MRR adalah rata-rata dari semua Reciprocal Rank untuk setiap query. Nilai ini memberikan gambaran umum seberapa baik model menemukan dokumen relevan dalam urutan pencarian.

MRR: 0.4942
Rata-rata Reciprocal Rank untuk keempat query adalah 0.4942.
Nilai ini mengindikasikan bahwa secara umum, model mampu menemukan dokumen relevan, tetapi performanya bervariasi. Dalam kasus ini:
"looking cake low calorie" sangat baik, dengan relevansi sempurna (dokumen ditemukan di posisi pertama).
Query lainnya gagal menemukan dokumen relevan.

### Top-10

In [15]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 1.3151
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 1.3151
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 4661
Score: 1.2817
Preview: easy baked fish fillet jane doerfer prep time 10 min total time 30 min serving 4 looking simple fish dinner skip frozen fillet try easy recipe baked fresh fish fillet little prep involved great lastmi...
----------------------------------------

In [16]:
df = dataset
df_pertanyaan = queries

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }

# Hitung Reciprocal Rank dan MRR
# rr_scores = calculate_rr(results_dict, ground_truth_dict)
# mrr_score = calculate_mrr(rr_scores)

# Tampilkan hasil evaluasi
print("\nHasil Evaluasi Reciprocal Rank (RR):")
print("="*50)
for query, rr in rr_scores.items():
    print(f"Query: {query} | RR: {rr:.4f}")

print("\nMean Reciprocal Rank (MRR):")
print(f"MRR: {mrr_score:.4f}")



Hasil Evaluasi Reciprocal Rank (RR):
Query: dinner recipe | RR: 1.0000
Query: recipe include chicken broccoli ingredient mediterranean diet classification | RR: 0.5000
Query: nutfree recipe | RR: 1.0000
Query: glutenfree recipe diet | RR: 1.0000
Query: vegan dinner recipe categorized lowcarb | RR: 0.1667
Query: highprotein recipe containing quinoa primary ingredient | RR: 1.0000
Query: asian dinner food | RR: 1.0000
Query: dessert america | RR: 0.2000
Query: dish free added sugar | RR: 1.0000
Query: dessert chocolate | RR: 1.0000
Query: high protein meal vegetarian | RR: 0.1429
Query: low sugar less 150 calorie drink suit diabetic | RR: 0.0000
Query: nobake dessert recipe simple quick make | RR: 0.2500
Query: provide meal prep recipe designed weight loss seafood | RR: 1.0000
Query: lowcarb high protein meal suitable keto diet | RR: 0.5000
Query: plantbased recipe high iron vegan | RR: 0.1667
Query: lowsodium soup fresh ingredient | RR: 0.5000
Query: 45 star rating smoothie bowl banana

### Top 20

In [17]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
top_20 = int(20)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 20 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 1.3151
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 1.3151
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 4661
Score: 1.2817
Preview: easy baked fish fillet jane doerfer prep time 10 min total time 30 min serving 4 looking simple fish dinner skip frozen fillet try easy recipe baked fresh fish fillet little prep involved great lastmi...
----------------------------------------

In [18]:
df = dataset
df_pertanyaan = queries

retrieval = BooleanBM25LRetrieval(df, df_pertanyaan)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }

# Hitung Reciprocal Rank dan MRR
rr_scores = calculate_rr(results_dict, ground_truth_dict)
mrr_score = calculate_mrr(rr_scores)

# Tampilkan hasil evaluasi
print("\nHasil Evaluasi Reciprocal Rank (RR):")
print("="*50)
for query, rr in rr_scores.items():
    print(f"Query: {query} | RR: {rr:.4f}")

print("\nMean Reciprocal Rank (MRR):")
print(f"MRR: {mrr_score:.4f}")



Hasil Evaluasi Reciprocal Rank (RR):
Query: dinner recipe | RR: 1.0000
Query: recipe include chicken broccoli ingredient mediterranean diet classification | RR: 0.5000
Query: nutfree recipe | RR: 1.0000
Query: glutenfree recipe diet | RR: 1.0000
Query: vegan dinner recipe categorized lowcarb | RR: 0.1667
Query: highprotein recipe containing quinoa primary ingredient | RR: 1.0000
Query: asian dinner food | RR: 1.0000
Query: dessert america | RR: 0.2000
Query: dish free added sugar | RR: 1.0000
Query: dessert chocolate | RR: 1.0000
Query: high protein meal vegetarian | RR: 0.1429
Query: low sugar less 150 calorie drink suit diabetic | RR: 0.0000
Query: nobake dessert recipe simple quick make | RR: 0.2500
Query: provide meal prep recipe designed weight loss seafood | RR: 1.0000
Query: lowcarb high protein meal suitable keto diet | RR: 0.5000
Query: plantbased recipe high iron vegan | RR: 0.1667
Query: lowsodium soup fresh ingredient | RR: 0.5000
Query: 45 star rating smoothie bowl banana

BM25L yg lama

top 5 
- Average Precision: 0.340
- Average Recall: 0.155

top 10
- Average Precision: 0.308
- Average Recall: 0.182

top 20
- Average Precision: 0.281
- Average Recall: 0.210

BM25L baru 

top 5 
- Average Precision: 0.303
- Average Recall: 0.130

top 10
- Average Precision: 0.282
- Average Recall: 0.151

top 20
- Average Precision: 0.262
- Average Recall: 0.180


# BM25 + Boolean

In [19]:
import re
from math import log

class BooleanBM25Retrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist() 
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        self.index = self._create_index()
        self.doc_lengths = self._calculate_doc_lengths()
        self.avgdl = sum(self.doc_lengths.values()) / len(self.doc_lengths)
    
        self.k1 = 1.5  # Typically BM25 uses 1.5 for k1
        self.b = 0.75  # Common value for b in BM25
    
    def _create_index(self):
        """Build inverted index for the documents based on 'Index'."""
        index = {}
        for doc_id, content in zip(self.doc_ids, self.documents):
            terms = content.lower().split()
            for term in terms:
                if term not in index:
                    index[term] = set()
                index[term].add(doc_id)  
        return index

    def _calculate_doc_lengths(self):
        """Calculate document lengths based on the number of words in each document."""
        return {doc_id: len(content.split()) for doc_id, content in zip(self.doc_ids, self.documents)}

    def _preprocess_query(self, query):
        """Preprocess query by replacing certain words with defined rules."""
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        """Parse boolean queries into positive and negative terms."""
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _calculate_bm25_score(self, term, doc_id):
        """Calculate BM25 score for a term in a document."""
        if term not in self.index or doc_id not in self.index[term]:
            return 0
        doc_terms = self.documents[self.doc_ids.index(doc_id)].lower().split()
        tf = doc_terms.count(term)
        df = len(self.index[term])
        N = len(self.documents)
        idf = log((N - df + 0.5) / (df + 0.5) + 1)  # BM25 formula for IDF
        dl = self.doc_lengths[doc_id]
        ctd = tf * (self.k1 + 1) / (tf + self.k1 * (1 - self.b + self.b * dl / self.avgdl))  # BM25 TF component
        return idf * ctd

    def search(self, query, top_n=5):
        """Perform a search and return top_n results with BM25 scoring."""
        positive_terms, negative_terms = self._parse_boolean_query(query)
        relevant_docs = set(self.doc_ids)
        
        # Apply negative filters to relevant documents
        for term in negative_terms:
            if term in self.index:
                relevant_docs -= self.index[term]
        
        # Calculate BM25 scores for each relevant document
        scores = {}
        if positive_terms:
            for doc_id in relevant_docs:
                score = sum(self._calculate_bm25_score(term, doc_id) for term in positive_terms)
                if score > 0:
                    scores[doc_id] = score
        else:
            for doc_id in relevant_docs:
                scores[doc_id] = self.doc_lengths[doc_id]
        
        # Rank documents by BM25 score
        ranked_results = sorted(scores.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results
    







### Top 5

In [20]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25Retrieval(df, df_pertanyaan)
top_5 = int(5)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_5)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)



Query: dinner recipe
Top 5 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 4.6691
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 4.6691
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 3380
Score: 4.2452
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

Ra

### Top 10

In [21]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25Retrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 4.6691
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 4.6691
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 3380
Score: 4.2452
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

R

In [22]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBM25Retrieval(df, df_pertanyaan)
top_20 = int(20)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 20 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 383
Score: 4.6691
Preview: easy chicken enchilada casserole katie webster prep time 20 min additional time 35 min total time 55 min serving 6 yield 1 casserole casserole make perfect mealprep dinner enchilada version exception ...
--------------------------------------------------

Rank 2:
Document ID: 3318
Score: 4.6691
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 3:
Document ID: 3380
Score: 4.2452
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

R

# QLM + Boolean

In [24]:
import re
from math import log

class QueryLikelihoodRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist() 
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        self.index = self._create_index()
        self.doc_lengths = self._calculate_doc_lengths()
        self.avgdl = sum(self.doc_lengths.values()) / len(self.doc_lengths)
    
        self.mu = 2000  # Smoothing parameter for Query Likelihood Model

        self.term_frequencies = self._calculate_term_frequencies()

    def _create_index(self):
        index = {}
        for doc_id, content in zip(self.doc_ids, self.documents):
            terms = content.lower().split()
            for term in terms:
                if term not in index:
                    index[term] = set()
                index[term].add(doc_id)  
        return index

    def _calculate_doc_lengths(self):
        return {doc_id: len(content.split()) for doc_id, content in zip(self.doc_ids, self.documents)}
    
    def _calculate_term_frequencies(self):
        """Calculate term frequencies for the entire collection"""
        term_freqs = {}
        total_terms = 0
        for doc in self.documents:
            terms = doc.lower().split()
            total_terms += len(terms)
            for term in terms:
                if term not in term_freqs:
                    term_freqs[term] = 0
                term_freqs[term] += 1
        return term_freqs, total_terms


    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)
    
    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms
    def _calculate_qlm_score(self, term, doc_id):
        if term not in self.index or doc_id not in self.index[term]:
            return 0
        
        # Get term frequency in the document
        doc_terms = self.documents[self.doc_ids.index(doc_id)].lower().split()
        term_count = doc_terms.count(term)
        
        # Calculate term probability in the document (with smoothing)
        doc_len = self.doc_lengths[doc_id]
        term_prob = (term_count + self.mu * self.term_frequencies[term] / self.term_frequencies[1]) / (doc_len + self.mu)
        
        return log(term_prob)


    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        relevant_docs = set(self.doc_ids)
        
        for term in negative_terms:
            if term in self.index:
                relevant_docs -= self.index[term]
        
        scores = {}
        for doc_id in relevant_docs:
            score = 0
            for term in positive_terms:
                score += self._calculate_qlm_score(term, doc_id)
            if score > 0:
                scores[doc_id] = score
        
        ranked_results = sorted(scores.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results


In [25]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = QueryLikelihoodRetrieval(df, df_pertanyaan)
top_20 = int(20)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)

TypeError: tuple indices must be integers or slices, not str

### QLM BLOM

# Jaccard + Boolean

In [24]:
import re

class BooleanJaccardRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()

        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        self.index = self._create_index()

    def _create_index(self):
        """Create an inverted index from the documents."""
        index = {}
        for doc_id, content in zip(self.doc_ids, self.documents):
            terms = set(content.lower().split())  # Use a set for unique terms
            for term in terms:
                if term not in index:
                    index[term] = set()
                index[term].add(doc_id)
        return index

    def _preprocess_query(self, query):
        """Preprocess query by replacing certain keywords with 'not'."""
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        """Parse the query into positive and negative terms."""
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _calculate_jaccard_similarity(self, query_terms, doc_id):
        """Calculate the Jaccard similarity between the query and a document."""
        doc_terms = set(self.documents[self.doc_ids.index(doc_id)].lower().split())
        intersection = query_terms.intersection(doc_terms)
        union = query_terms.union(doc_terms)
        if len(union) == 0:
            return 0
        return len(intersection) / len(union)

    def search(self, query, top_n=5):
        """Search for relevant documents using Jaccard similarity."""
        positive_terms, negative_terms = self._parse_boolean_query(query)
        query_terms = set(positive_terms)  # Convert positive terms to a set
        
        # Start with all documents as relevant
        relevant_docs = set(self.doc_ids)
        
        # Remove documents containing negative terms
        for term in negative_terms:
            if term in self.index:
                relevant_docs -= self.index[term]

        # Calculate Jaccard similarity scores for each document
        scores = {}
        for doc_id in relevant_docs:
            score = self._calculate_jaccard_similarity(query_terms, doc_id)
            if score > 0:
                scores[doc_id] = score

        # Sort by Jaccard similarity score and return top_n results
        ranked_results = sorted(scores.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results


### Top 5

In [25]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanJaccardRetrieval(df, df_pertanyaan)
top_5 = int(5)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_5)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 5 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.1250
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 5059
Score: 0.1250
Preview: basic overnight oat recipe & # 39
--------------------------------------------------

Rank 3:
Document ID: 671
Score: 0.1000
Preview: avocado toast recipe youll ever need & # 43
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.0769
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

Rank 5:
Document ID: 2811
Score: 0.0690
Preview: shredded chicken taco eatingwell test kitchen prep time 15 min additional time 2 hr 45 min total time 3 hr serving 8 yield 16 taco taco r

### Top 10

In [26]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanJaccardRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.1250
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 5059
Score: 0.1250
Preview: basic overnight oat recipe & # 39
--------------------------------------------------

Rank 3:
Document ID: 671
Score: 0.1000
Preview: avocado toast recipe youll ever need & # 43
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.0769
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

Rank 5:
Document ID: 2811
Score: 0.0690
Preview: shredded chicken taco eatingwell test kitchen prep time 15 min additional time 2 hr 45 min total time 3 hr serving 8 yield 16 taco taco 

### Top 20

In [27]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanJaccardRetrieval(df, df_pertanyaan)
top_20 = int(20)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 20 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.1250
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 5059
Score: 0.1250
Preview: basic overnight oat recipe & # 39
--------------------------------------------------

Rank 3:
Document ID: 671
Score: 0.1000
Preview: avocado toast recipe youll ever need & # 43
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.0769
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
--------------------------------------------------

Rank 5:
Document ID: 2811
Score: 0.0690
Preview: shredded chicken taco eatingwell test kitchen prep time 15 min additional time 2 hr 45 min total time 3 hr serving 8 yield 16 taco taco 

# TF-IDF

In [8]:
import re
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

class BooleanTFIDFRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        # Initialize and fit TF-IDF vectorizer
        self.vectorizer = TfidfVectorizer()
        self.doc_term_matrix = self.vectorizer.fit_transform(self.documents)

    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _calculate_tfidf_similarity(self, query_vector, doc_vector):
        return cosine_similarity(query_vector, doc_vector.reshape(1, -1))[0][0]

    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        
        # Create query string
        query_str = ' '.join(positive_terms)
        
        # Transform query to TF-IDF space
        query_vector = self.vectorizer.transform([query_str])
        
        # Calculate similarities
        similarities = {}
        for i, doc_id in enumerate(self.doc_ids):
            # Check if document contains any negative terms
            doc_text = self.documents[i].lower()
            if any(term.lower() in doc_text for term in negative_terms):
                continue
                
            similarity = self._calculate_tfidf_similarity(query_vector, self.doc_term_matrix[i])
            if similarity > 0:
                similarities[doc_id] = similarity
        
        # Sort by similarity score
        ranked_results = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results

In [27]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanTFIDFRetrieval(df, df_pertanyaan)
top_5 = int(5)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_5)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 5 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.2674
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 1028
Score: 0.2439
Preview: turkey dinner skillet eatingwell test kitchen prep time 40 min total time 40 min serving 2 yield 4 cup & # 39
--------------------------------------------------

Rank 3:
Document ID: 3318
Score: 0.1925
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.1664
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39
-

In [28]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanTFIDFRetrieval(df, df_pertanyaan)
top_10= int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.2674
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 1028
Score: 0.2439
Preview: turkey dinner skillet eatingwell test kitchen prep time 40 min total time 40 min serving 2 yield 4 cup & # 39
--------------------------------------------------

Rank 3:
Document ID: 3318
Score: 0.1925
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.1664
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39


In [29]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanTFIDFRetrieval(df, df_pertanyaan)
top_20 = int(20)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_20)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 20 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4648
Score: 0.2674
Preview: lemongarlic dump dinner chicken potato & amp
--------------------------------------------------

Rank 2:
Document ID: 1028
Score: 0.2439
Preview: turkey dinner skillet eatingwell test kitchen prep time 40 min total time 40 min serving 2 yield 4 cup & # 39
--------------------------------------------------

Rank 3:
Document ID: 3318
Score: 0.1925
Preview: slowcooker chicken noodle soup mealprep freezer pack hilary meyer prep time 25 min additional time 4 hr 5 min total time 4 hr 30 min serving 8 yield 8 serving chicken noodle soup recipe utilize crock ...
--------------------------------------------------

Rank 4:
Document ID: 3380
Score: 0.1664
Preview: mealprep cilantrolime chicken bowl carolyn casner prep time 45 min total time 45 min serving 4 yield 4 serving prep four serving easy recipe readytoeat dinner packable lunch rest week & # 39


# Semantic

# LSI+ Boolean

In [17]:
import re
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics.pairwise import cosine_similarity

class BooleanLSIRetrieval:
    def __init__(self, df, df_pertanyaan, n_components=100):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()
        self.n_components = min(n_components, len(self.documents) - 1)
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        # Initialize and fit TF-IDF vectorizer
        self.vectorizer = TfidfVectorizer()
        self.doc_term_matrix = self.vectorizer.fit_transform(self.documents)
        
        # Perform LSI using TruncatedSVD
        self.lsi = TruncatedSVD(n_components=self.n_components)
        self.doc_topic_matrix = self.lsi.fit_transform(self.doc_term_matrix)
        
    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _calculate_lsi_similarity(self, query_vector, doc_vector):
        return cosine_similarity(query_vector, doc_vector.reshape(1, -1))[0][0]

    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        
        # Create query string
        query_str = ' '.join(positive_terms)
        
        # Transform query to LSI space
        query_vector = self.vectorizer.transform([query_str])
        query_topic = self.lsi.transform(query_vector)
        
        # Calculate similarities
        similarities = {}
        for i, doc_id in enumerate(self.doc_ids):
            # Check if document contains any negative terms
            doc_text = self.documents[i].lower()
            if any(term.lower() in doc_text for term in negative_terms):
                continue
                
            similarity = self._calculate_lsi_similarity(query_topic, self.doc_topic_matrix[i])
            if similarity > 0:
                similarities[doc_id] = similarity
        
        # Sort by similarity score
        ranked_results = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results

In [18]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanLSIRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 4028
Score: 0.5898
Preview: cheesy meatball casserole liv dansky active time 20 min total time 1 hr serving 8 cheesy meatball casserole family favorite basil adding fresh flavor learn make easy casserole dinner [ nutfree healthy...
--------------------------------------------------

Rank 2:
Document ID: 3025
Score: 0.5522
Preview: quick king ranch chicken casserole julia levy active time 25 min additional time 5 min total time 30 min serving 4 yield 5 cup chicken casserole recipe easy weeknightfriendly dinner learn make king ra...
--------------------------------------------------

Rank 3:
Document ID: 2945
Score: 0.5475
Preview: chipotle ranch chicken casserole eatingwell test kitchen prep time 20 min additional time 40 min total time 1 hr serving 8 yield 8 serving simplify weeknight dinnertime transforming leftover slowcooke...
---------------------------------------

### Word2Vec

In [20]:
import re
import numpy as np
from gensim.models import Word2Vec
from sklearn.metrics.pairwise import cosine_similarity

class BooleanWord2VecRetrieval:
    def __init__(self, df, df_pertanyaan, vector_size=100, window=5, min_count=1):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        # Prepare sentences for Word2Vec
        self.sentences = [doc.split() for doc in self.documents]
        
        # Train Word2Vec model
        self.word2vec = Word2Vec(sentences=self.sentences,
                                vector_size=vector_size,
                                window=window,
                                min_count=min_count,
                                workers=4)
        
        # Create document vectors by averaging word vectors
        self.doc_vectors = self._create_document_vectors()
        
    def _create_document_vectors(self):
        doc_vectors = []
        for doc in self.documents:
            words = doc.split()
            word_vectors = []
            for word in words:
                if word in self.word2vec.wv:
                    word_vectors.append(self.word2vec.wv[word])
            if word_vectors:
                doc_vectors.append(np.mean(word_vectors, axis=0))
            else:
                doc_vectors.append(np.zeros(self.word2vec.vector_size))
        return np.array(doc_vectors)

    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _get_query_vector(self, query_terms):
        word_vectors = []
        for term in query_terms:
            if term in self.word2vec.wv:
                word_vectors.append(self.word2vec.wv[term])
        if word_vectors:
            return np.mean(word_vectors, axis=0).reshape(1, -1)
        return np.zeros((1, self.word2vec.vector_size))

    def _calculate_similarity(self, query_vector, doc_vector):
        return cosine_similarity(query_vector, doc_vector.reshape(1, -1))[0][0]

    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        
        # Get query vector
        query_vector = self._get_query_vector(positive_terms)
        
        # Calculate similarities
        similarities = {}
        for i, doc_id in enumerate(self.doc_ids):
            # Check if document contains any negative terms
            doc_text = self.documents[i].lower()
            if any(term.lower() in doc_text for term in negative_terms):
                continue
                
            similarity = self._calculate_similarity(query_vector, self.doc_vectors[i])
            if similarity > 0:
                similarities[doc_id] = similarity
        
        # Sort by similarity score
        ranked_results = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results

In [21]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanWord2VecRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 671
Score: 0.6945
Preview: avocado toast recipe youll ever need & # 43
--------------------------------------------------

Rank 2:
Document ID: 1802
Score: 0.5776
Preview: skinny guacamole stacy fraser cook time 20 min total time 20 min serving 4 yield 4 serving 1/2 cup delicious guacamole recipe replaces half amount highcalorie avocado traditional guacamole recipe stea...
--------------------------------------------------

Rank 3:
Document ID: 1266
Score: 0.5292
Preview: citrusarugula salad liz mervosh prep time 10 min total time 10 min serving 4 yield 6 cup easy salad recipe make stunning side dish anything & # 39
--------------------------------------------------

Rank 4:
Document ID: 4134
Score: 0.5158
Preview: roasted barramundi asparagus gremolata julia clancy prep time 25 min total time 25 min serving 4 yield 4 serving barramundi aka asian sea bass mild white fi

In [22]:
import re
import numpy as np
import torch
from transformers import BertTokenizer, BertModel
from sklearn.metrics.pairwise import cosine_similarity

class BooleanBERTRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        # Load BERT tokenizer and model
        self.tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
        self.model = BertModel.from_pretrained('bert-base-uncased')
        self.model.eval()  # Set the model to evaluation mode

        # Create document vectors using BERT
        self.doc_vectors = self._create_document_vectors()
        
    def _create_document_vectors(self):
        doc_vectors = []
        for doc in self.documents:
            inputs = self.tokenizer(doc, return_tensors='pt', padding=True, truncation=True)
            with torch.no_grad():
                outputs = self.model(**inputs)
            # Use the mean of the last hidden state as the document vector
            doc_vector = outputs.last_hidden_state.mean(dim=1).numpy()
            doc_vectors.append(doc_vector)
        return np.concatenate(doc_vectors)

    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _get_query_vector(self, query_terms):
        query_text = ' '.join(query_terms)
        inputs = self.tokenizer(query_text, return_tensors='pt', padding=True, truncation=True)
        with torch.no_grad():
            outputs = self.model(**inputs)
        # Use the mean of the last hidden state as the query vector
        return outputs.last_hidden_state.mean(dim=1).numpy()

    def _calculate_similarity(self, query_vector, doc_vector):
        return cosine_similarity(query_vector, doc_vector.reshape(1, -1))[0][0]

    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        
        # Get query vector
        query_vector = self._get_query_vector(positive_terms)
        
        # Calculate similarities
        similarities = {}
        for i, doc_id in enumerate(self.doc_ids):
            # Check if document contains any negative terms
            doc_text = self.documents[i].lower()
            if any(term.lower() in doc_text for term in negative_terms):
                continue
                
            similarity = self._calculate_similarity(query_vector, self.doc_vectors[i])
            if similarity > 0:
                similarities[doc_id] = similarity
        
        # Sort by similarity score
        ranked_results = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results

In [23]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanBERTRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

c:\Users\rashi\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:147: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\rashi\.cache\huggingface\hub\models--bert-base-uncased. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]


Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 2056
Score: 0.7341
Preview: egg salad & amp
--------------------------------------------------

Rank 2:
Document ID: 2057
Score: 0.7341
Preview: egg salad & amp
--------------------------------------------------

Rank 3:
Document ID: 3848
Score: 0.7329
Preview: baked tomato & amp
--------------------------------------------------

Rank 4:
Document ID: 2363
Score: 0.7323
Preview: turkey pasta & amp
--------------------------------------------------

Rank 5:
Document ID: 4045
Score: 0.7281
Preview: baked fish & amp
--------------------------------------------------

Rank 6:
Document ID: 551
Score: 0.7160
Preview: tuna salad & amp
--------------------------------------------------

Rank 7:
Document ID: 1949
Score: 0.7126
Preview: sausage & amp
--------------------------------------------------

Rank 8:
Document ID: 3101
Score: 0.7126
Preview: sausage & amp
---------------

In [24]:
import numpy as np
import torch
from transformers import MPNetTokenizer, MPNetModel
from sklearn.metrics.pairwise import cosine_similarity

class BooleanMPNetRetrieval:
    def __init__(self, df, df_pertanyaan):
        if "processed_text" not in df.columns:
            raise ValueError("The column 'processed_text' does not exist in the documents DataFrame.")
        if "processed_pertanyaan" not in df_pertanyaan.columns:
            raise ValueError("The column 'processed_pertanyaan' does not exist in the queries DataFrame.")
        if "Index" not in df.columns:
            raise ValueError("The column 'Index' does not exist in the documents DataFrame.")
        
        self.documents = df["processed_text"].tolist()
        self.queries = df_pertanyaan["processed_pertanyaan"].tolist()
        self.doc_ids = df["Index"].tolist()
        
        self.query_rules = {
            'without': 'not',
            'but': 'not',
            'no': 'not'
        }

        # Load MPNet tokenizer and model
        self.tokenizer = MPNetTokenizer.from_pretrained('microsoft/mpnet-base')
        self.model = MPNetModel.from_pretrained('microsoft/mpnet-base')
        self.model.eval()  # Set the model to evaluation mode

        # Create document vectors using MPNet
        self.doc_vectors = self._create_document_vectors()
        
    def _create_document_vectors(self):
        doc_vectors = []
        for doc in self.documents:
            inputs = self.tokenizer(doc, return_tensors='pt', padding=True, truncation=True)
            with torch.no_grad():
                outputs = self.model(**inputs)
            # Use the mean of the last hidden state as the document vector
            doc_vector = outputs.last_hidden_state.mean(dim=1).numpy()
            doc_vectors.append(doc_vector)
        return np.concatenate(doc_vectors)

    def _preprocess_query(self, query):
        query_terms = query.split()
        processed_terms = []
        for term in query_terms:
            if term in self.query_rules:
                processed_terms.append(self.query_rules[term])
            else:
                processed_terms.append(term)
        return ' '.join(processed_terms)

    def _parse_boolean_query(self, query):
        processed_query = self._preprocess_query(query)
        terms = processed_query.split()
        positive_terms = []
        negative_terms = []
        i = 0
        while i < len(terms):
            if terms[i] == 'not' and i + 1 < len(terms):
                negative_terms.append(terms[i + 1])
                i += 2
            else:
                positive_terms.append(terms[i])
                i += 1
        return positive_terms, negative_terms

    def _get_query_vector(self, query_terms):
        query_text = ' '.join(query_terms)
        inputs = self.tokenizer(query_text, return_tensors='pt', padding=True, truncation=True)
        with torch.no_grad():
            outputs = self.model(**inputs)
        # Use the mean of the last hidden state as the query vector
        return outputs.last_hidden_state.mean(dim=1).numpy()

    def _calculate_similarity(self, query_vector, doc_vector):
        return cosine_similarity(query_vector, doc_vector.reshape(1, -1))[0][0]

    def search(self, query, top_n=5):
        positive_terms, negative_terms = self._parse_boolean_query(query)
        
        # Get query vector
        query_vector = self._get_query_vector(positive_terms)
        
        # Calculate similarities
        similarities = {}
        for i, doc_id in enumerate(self.doc_ids):
            # Check if document contains any negative terms
            doc_text = self.documents[i].lower()
            if any(term.lower() in doc_text for term in negative_terms):
                continue
                
            similarity = self._calculate_similarity(query_vector, self.doc_vectors[i])
            if similarity > 0:
                similarities[doc_id] = similarity
        
        # Sort by similarity score
        ranked_results = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_n]
        return ranked_results

In [25]:
ground_truth_dict = {}
for i, query in enumerate(queries["processed_pertanyaan"].tolist()):
    key = f"pertanyaan {i+1}".lower()  
    gtruth_keys = {k.lower(): k for k in gtruth.keys()}  
    
    if key in gtruth_keys:  
        original_key = gtruth_keys[key] 
        ground_truth_dict[query.lower()] = gtruth[original_key]
    else:
        print(f"Warning: Ground truth key '{key}' not found for query '{query}'")
df = dataset  
df_pertanyaan = queries  

retrieval = BooleanMPNetRetrieval(df, df_pertanyaan)
top_10 = int(10)
results_dict = {}
for query in retrieval.queries:
    results = retrieval.search(query, top_n=top_10)
    display_search_results(retrieval, query, results)
    
    results_dict[query] = {
        'Index': [doc_id for doc_id, score in results],
        'Scores': [score for doc_id, score in results],
    }
print("\nHasil Evaluasi:")
print("="*50)
avg_precision, avg_recall = calculate_metrics(results_dict, ground_truth_dict)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

c:\Users\rashi\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:147: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\rashi\.cache\huggingface\hub\models--microsoft--mpnet-base. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/472k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/493 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/532M [00:00<?, ?B/s]

Some weights of MPNetModel were not initialized from the model checkpoint at microsoft/mpnet-base and are newly initialized: ['mpnet.pooler.dense.bias', 'mpnet.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



Query: dinner recipe
Top 10 hasil pencarian:
--------------------------------------------------

Rank 1:
Document ID: 551
Score: 0.8133
Preview: tuna salad & amp
--------------------------------------------------

Rank 2:
Document ID: 2056
Score: 0.8114
Preview: egg salad & amp
--------------------------------------------------

Rank 3:
Document ID: 2057
Score: 0.8114
Preview: egg salad & amp
--------------------------------------------------

Rank 4:
Document ID: 4950
Score: 0.8030
Preview: mixed green salad chicken & amp
--------------------------------------------------

Rank 5:
Document ID: 3172
Score: 0.8030
Preview: pesto & amp
--------------------------------------------------

Rank 6:
Document ID: 4662
Score: 0.8029
Preview: seafood & amp
--------------------------------------------------

Rank 7:
Document ID: 1011
Score: 0.8004
Preview: goat cheese & amp
--------------------------------------------------

Rank 8:
Document ID: 1325
Score: 0.7992
Preview: cream cheese & amp
---